# オブジェクト指向回 演習問題

## 必要なmoduleのimport

In [ ]:
from abc import ABC, abstractmethod
from typing import Literal, Optional
from typing_extensions import override

## Entityの定義

In [ ]:
class Entity:
    def __init__(self, is_enemy: bool, name: str, hp: int, attack: int):
        self.__is_enemy = is_enemy
        self.__name = name
        self.__hp = hp
        self.__attack = attack

    @property
    def is_enemy(self):
        return self.__is_enemy

    @property
    def name(self):
        return self.__name

    @property
    def hp(self):
        return self.__hp

    @hp.setter
    def hp(self, value: int):
        # 負の数にならないようにする
        self.__hp = max(0, value)

    @property
    def attack(self):
        return self.__attack

    def commands(self):
        return [AttackCommand()]


class Battle:
    enemies: list[Entity]
    players: list[Entity]

    def __init__(self, players: list[Entity], enemies: list[Entity]):
        self.players = players
        self.enemies = enemies

    def print_status(self):
        for player in self.players:
            print(f"自 {player.name}: HP={player.hp}")
        for enemy in self.enemies:
            print(f"敵 {enemy.name}: HP={enemy.hp}")
        print("----------")

    def is_settled(self) -> Optional[Literal["player", "enemies"]]:
        if all(enemy.hp <= 0 for enemy in self.enemies):
            return "player"
        if all(player.hp <= 0 for player in self.players):
            return "enemies"
        return None

    def all_entities(self):
        return [*self.players, *self.enemies]

    def start(self):
        turn = "player"
        while not (judgement := self.is_settled()):
            self.print_status()
            if turn == "player":
                self.player_turn()
                turn = "enemies"
            else:
                self.enemies_turn()
                turn = "player"

        if judgement == "player":
            print("プレイヤーの勝ち")
        else:
            print("プレイヤーの負け")

    def player_turn(self):
        # コマンドを表示
        decision = []
        for player in self.players:
            if player.hp == 0:
                continue

            print(f"{player.name}のターン")
            commands = player.commands()
            for id, command in enumerate(commands):
                print(f"{id}: {command.name}")

            # コマンドを選択
            command = commands[ask_int("どうする？> ", 0, len(commands) - 1)]
            print("----------")

            # ターゲットを選択
            all_entities = self.all_entities()
            targets = command.possible_targets(all_entities, player)
            for id, target in enumerate(targets):
                print(f"{id}: {target.name} HP={target.hp}")
            target = targets[ask_int("誰に？> ", 0, len(targets) - 1)]
            print("----------")
            decision.append((player, command, target))

        for player, command, target in decision:
            command.execute(player, target)

    def enemies_turn(self):
        # とりあえず敵は攻撃するだけ
        for enemy in self.enemies:
            if enemy.hp == 0:
                continue
            # 生存している最初のプレイヤーに攻撃
            player = next(player for player in self.players if player.hp > 0)
            enemy.commands()[0].execute(enemy, player)

def ask_int(prompt: str, min_value: int, max_value: int) -> int:
    while True:
        try:
            value = int(input(prompt))
            if min_value <= value <= max_value:
                return value
        except (KeyboardInterrupt, EOFError):
            raise
        except:
            pass
        print("範囲内の数字を入力してください")


# プレイヤー
class Player(Entity):
    def __init__(self, name: str, hp: int, attack: int):
        super().__init__(False, name, hp, attack)

    def commands(self):
        return [AttackCommand(), HealCommand()]


# 敵
class EnemySlime(Entity):
    def __init__(self):
        super().__init__(True, "スライム", 10, 1)


class EnemyGoblin(Entity):
    def __init__(self):
        super().__init__(True, "ゴブリン", 20, 5)


## コマンドの定義

In [ ]:
class Command(ABC):
    def __init__(self, name: str):
        self.__name = name

    @property
    def name(self):
        return self.__name

    @abstractmethod
    def possible_targets(self, entities: list[Entity], operator: Entity):
        "このコマンドの対象となりうるエンティティを列挙する"
        ...

    @abstractmethod
    def execute(self, operator: Entity, target: Entity):
        "operatorがこのコマンドをtargetに対して実行する"
        ...

class AttackCommand(Command):
    def __init__(self):
        super().__init__("攻撃")

    @override
    def possible_targets(self, entities: list[Entity], operator: Entity):
        # 自分と違うサイドのエンティティを攻撃可能
        return [e for e in entities if e.is_enemy != operator.is_enemy]

    @override
    def execute(self, operator: Entity, target: Entity):
        print(f"{operator.name}の攻撃！")
        print(f"{target.name}に{operator.attack}のダメージ")
        target.hp -= operator.attack


class HealCommand(Command):
    def __init__(self):
        super().__init__("回復")

    @override
    def possible_targets(self, entities: list[Entity], operator: Entity):
        # 自分自身のみ回復可能
        return [operator]

    @override
    def execute(self, operator: Entity, target: Entity):
        print(f"{operator.name}の回復！")
        print(f"{target.name}のHPが10回復した")
        target.hp += 10


## プレイ

In [ ]:
players: list[Entity] = [
    Player("ゆうしゃ", 30, 10),
]
enemies: list[Entity] = [
    EnemySlime(),
    EnemyGoblin(),
]
battle = Battle(players, enemies)
battle.start()